In [16]:
import folium

print(folium.__file__)
print(folium.__version__)

C:\Users\Kamol\Anaconda3\lib\site-packages\folium\__init__.py
0.5.0


In [17]:
import re
import mplleaflet
import matplotlib.pyplot as plt
import numpy as np
from collections import Counter
import pygeohash as gh
from datetime import datetime
import ast
import random
import pickle
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
import string
import sklearn.mixture as mix
import nltk
import pandas as pd
import os
import glob

punct=set(string.punctuation)
stop_words = set(stopwords.words('english'))
bad_words=["b","''","n't","https","'s","'ve","rt","b'rt"]

In [18]:
inpfile= r"E:\Kamol_Data\AfterClassMod\results_heuristic.csv"
    
df=pd.read_csv(inpfile,parse_dates=['evacuation_time_cor','return_time_cor'])
df_1=df[df["evac_cat_cor"]=='1']
df_1['evacuation_time_cor']=pd.to_datetime(df_1['evacuation_time_cor'])
df_1['return_time_cor']=pd.to_datetime(df_1['return_time_cor'])

df_home=dict(zip(list(df_1['user_id']),list(df_1['home'])))
df_office=dict(zip(list(df_1['user_id']),list(df_1['office'])))

C:\Users\Kamol\Anaconda3\lib\site-packages\ipykernel\__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
C:\Users\Kamol\Anaconda3\lib\site-packages\ipykernel\__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [19]:
indir = r"E:\Kamol_Data\Back_Track"
os.chdir(indir)
fileList=glob.glob("*csv")

In [25]:
with open("E:\Kamol_Data\id_to_file_mapper.pickle",'rb')  as fp:
    id_to_file_mapper=pickle.load(fp)

In [26]:
def Location_perser(row):
    lat='None'
    lon='None'
    print("\n",row['tweet.place'])
    
    try:

        if str(row['Tweet_Coordinates'])!='nan':
            coord_dict=ast.literal_eval(row['Tweet_Coordinates'])
            lat=coord_dict['coordinates'][1]
            lon=coord_dict['coordinates'][0]
    #            print(row['Tweet_Coordinates'],'lat:', lat, 'lon:', lon)
     
    
        if lat=='None':                   
            if str(row['tweet.place'])!='nan':
                
                x=row['tweet.place'].split("[[[")[1].split("]]]")[0].split("]")
    
                x2=",".join(x).split("[")
                x2=[(float(x.split(",")[0]),float(x.split(",")[1])) for x in x2]
                
                lon=(x2[0][0]+x2[1][0])/2
                lat=(x2[0][1]+x2[2][1])/2
    except:
        pass

    return tuple((lat,lon))


            
            
#for user_file in category_dict['remotely_evacuated'][13:14]:

for user_file in list(df_1['user_id'])[30:31]:    
    filename=id_to_file_mapper[str(user_file)]    
    df_write=pd.read_csv(filename,encoding='utf-8',parse_dates=['created_at'])
    df_write=df_write.sort_values(by='created_at') 
#    df_write=df_write.set_index('created_at')
    
#    date_mask = (df_write.index > datetime(2017, 1, 1)) & (df_write.index < datetime(2017, 10, 30))
#    dates = df_write.index[date_mask]
#    df_show= df_write.loc[dates]
    df_show=df_write[(df_write['created_at'] > datetime(2017, 9, 3)) & (df_write['created_at'] < datetime(2017, 9, 15))]

    df_show=df_show[['created_at','text','Tweet_Coordinates','tweet.place']]
    df_show.reset_index(drop=True, inplace=True)
    df_show_text=df_show[['text']]
    df_show['lat']=df_show.apply(lambda x: Location_perser(x)[0], axis=1)
    df_show['lon']=df_show.apply(lambda x: Location_perser(x)[1], axis=1)
    df_show=df_show[['created_at','text','lat','lon']]
            

if df_home[user_file]=='Missing' or str(df_home[user_file])=='nan':
    home_lat,home_lon= gh.decode(df_office[user_file])
    office_lat,office_lon= gh.decode(df_office[user_file])
    
elif df_office[user_file]=='Missing' or str(df_office[user_file])=='nan':
    home_lat,home_lon=gh.decode(df_home[user_file])
    office_lat,office_lon=gh.decode(df_home[user_file])
else:
    home_lat,home_lon=gh.decode(df_home[user_file])
    office_lat,office_lon= gh.decode(df_office[user_file])


 nan

 Place(id='fa8f8f24dc772cc0', country_code='US', contained_within=[], name='Pompano Beach', _api=<tweepy.api.API object at 0x0000020E9D983DA0>, bounding_box=BoundingBox(type='Polygon', coordinates=[[[-80.1955611, 26.206136], [-80.0817297, 26.206136], [-80.0817297, 26.2976539], [-80.1955611, 26.2976539]]], _api=<tweepy.api.API object at 0x0000020E9D983DA0>), place_type='city', country='United States', full_name='Pompano Beach, FL', attributes={}, url='https://api.twitter.com/1.1/geo/id/fa8f8f24dc772cc0.json')

 Place(id='fa8f8f24dc772cc0', country_code='US', contained_within=[], name='Pompano Beach', _api=<tweepy.api.API object at 0x0000020E9D983DA0>, bounding_box=BoundingBox(type='Polygon', coordinates=[[[-80.1955611, 26.206136], [-80.0817297, 26.206136], [-80.0817297, 26.2976539], [-80.1955611, 26.2976539]]], _api=<tweepy.api.API object at 0x0000020E9D983DA0>), place_type='city', country='United States', full_name='Pompano Beach, FL', attributes={}, url='https://api.twitter.com

 nan

 Place(id='fa8f8f24dc772cc0', country_code='US', contained_within=[], name='Pompano Beach', _api=<tweepy.api.API object at 0x0000020E9D983DA0>, bounding_box=BoundingBox(type='Polygon', coordinates=[[[-80.1955611, 26.206136], [-80.0817297, 26.206136], [-80.0817297, 26.2976539], [-80.1955611, 26.2976539]]], _api=<tweepy.api.API object at 0x0000020E9D983DA0>), place_type='city', country='United States', full_name='Pompano Beach, FL', attributes={}, url='https://api.twitter.com/1.1/geo/id/fa8f8f24dc772cc0.json')

 nan

 Place(id='fa8f8f24dc772cc0', country_code='US', contained_within=[], name='Pompano Beach', _api=<tweepy.api.API object at 0x0000020E9D983DA0>, bounding_box=BoundingBox(type='Polygon', coordinates=[[[-80.1955611, 26.206136], [-80.0817297, 26.206136], [-80.0817297, 26.2976539], [-80.1955611, 26.2976539]]], _api=<tweepy.api.API object at 0x0000020E9D983DA0>), place_type='city', country='United States', full_name='Pompano Beach, FL', attributes={}, url='https://api.twitte

In [28]:
import folium
import pandas as pd

feature_group = folium.FeatureGroup(name='Real-Time Data')
feature_group2 = folium.FeatureGroup(name='Analytics')
feature_group3 = folium.FeatureGroup(name='Crowd-sourced Twitter data')
feature_group4 = folium.FeatureGroup(name='Crash data')
feature_group5 = folium.FeatureGroup(name='Prediction Based on Analytics')







df_show=df_show[df_show['lat']!='None']        
lat_lon=[]

for index, row in df_show.iterrows():
    lat_lon.append([row['lat'],row['lon']])
    


m = folium.Map([27.5, -81.5], zoom_start=4)


#import branca.colormap as cm
#colormap = cm.linear.Set1.scale(0, 35).to_step(2)
#colormap.caption = '----Home----- Office -----  '
#m.add_child(colormap)



#folium.CircleMarker(
#    location=[38.5, -79.4],
#    radius=30,
#    fill=False,
#    icon=folium.Icon(prefix='fa',color='red',icon='fa-industry fa-3x'),
#    popup=folium.Popup('inline explicit Popup')
#).add_to(feature_group)
def text_cleaner(texts):
#    print("---1----: ",texts)
    texts=texts.split("'")[1]
#    print("\n---2----: ",texts)
    word_split=word_tokenize(texts)
    filtered_word1=[w.lower() for w in word_split if not w in punct]
    filtered_word2=[w for w in filtered_word1 if not w in stop_words]
    filtered_word2=[w for w in filtered_word2 if not type(w ) in [type(5.0), type(5)]]
    filtered_word3=[w for w in filtered_word2 if not w.lower() in bad_words]
#        print(filtered_word3)
    filtered_sent=" ".join(filtered_word3)
    
    filtered_text=" ".join(filter(lambda x:x[0]!='#', filtered_sent.split()))
    filtered_text=" ".join(filter(lambda x:x[0]!='/', filtered_text.split()))
    filtered_text=" ".join(filter(lambda x:x[0]!="\\", filtered_text.split()))


    filtered_text=" ".join(filter(lambda x:x[0]!='https', filtered_text.split()))
#    print(filtered_text)
#    filtered_text="".join(word for word in filtered_text if "\\" not in r"%r" % word)
    filtered_text="".join(word for word in filtered_text if "\\" not in r"%r" % word)
#    print(filtered_text)
#    print("\n---final----: ",texts)   
    return filtered_text 
    
#----- For Home----------
df = df_show[(df_show['lat']==home_lat) & (df_show['lon']==home_lon)]             
if len(df)>0:             
    df=df.reset_index()
    df['text']=df.apply(lambda x: text_cleaner(x.text), axis=1)
    df=df[['created_at','text']].astype(str)
    df=df.set_index('created_at')
    html = df.to_html()
    popup = folium.Popup(html,max_width=800)
else:
    popup='NO Tweets Recently'  

folium.Marker([home_lat, home_lon],icon=folium.Icon(prefix='fa',color='green',icon='fa-home'), popup=popup).add_to(feature_group)


#----- For Office ----------

df = df_show[(df_show['lat']==office_lat) & (df_show['lon']==office_lon)]

if len(df)>0:             
    df=df.reset_index()
    df['text']=df.apply(lambda x: text_cleaner(x.text), axis=1)
    df=df[['created_at','text']].astype(str)
    df=df.set_index('created_at')
    html = df.to_html()
    popup = folium.Popup(html,max_width=800)
else:
    popup='NO Tweets Recently'

f_lat=27.698681999999998
f_lon=-83.804475
    
folium.Marker([office_lat, office_lon],icon=folium.Icon(prefix='fa',color='red',icon='fa-industry fa-3x'), popup=popup).add_to(feature_group3)
    
#folium.CircleMarker([ 27.6648274, -81.5157535],radius=10,fill=True, fill_color='red',popup='original').add_to(feature_group3)  
#folium.CircleMarker([f_lat, f_lon],radius=10,fill=True, fill_color='green',popup='f_lat').add_to(feature_group3)
#folium.CircleMarker([32.1656221, -82.9000751],radius=10,fill=True, fill_color='red').add_to(feature_group3)
#folium.CircleMarker([g_lat, g_lon],radius=10,fill=True, fill_color='yellow').add_to(feature_group3)

  
f_lat=27.698681999999998
f_lon=-83.804475



for i in lat_lon:
#    df = pd.DataFrame(data=[['apple', 'oranges'], ['other', 'stuff']], columns=['cats', 'dogs'])
    df = df_show[(df_show['lat']==i[0]) & (df_show['lon']==i[1])]
                 
#    df=df.astype(str)
    df=df.reset_index()
    df['text']=df.apply(lambda x: text_cleaner(x.text), axis=1)
    
    df=df[['created_at','text']].astype(str)
    df=df.set_index('created_at')
#    df['lat']=['kamol' for i in range(len(df))]
#    df['lon']=['kamol' for i in range(len(df))]
    html = df.to_html()
    
    popup = folium.Popup(html,max_width=800)    
    folium.Marker(i, popup=popup).add_to(feature_group2)


#ls = folium.PolyLine(
#    locations=[[43, 7], [43, 13], [47, 13], [47, 7], [43, 7]],
#    color='red'
#)

ls = folium.PolyLine(
    locations=lat_lon,
    color='black',
    weight=2,
    opacity=0.2
)

ls.add_child(folium.Popup('outline Popup on Polyline'))
ls.add_to(feature_group2)

#gj = folium.GeoJson(
#    data={
#        'type': 'Polygon',
#        'coordinates': [[[27, 43], [33, 43], [33, 47], [27, 47]]]
#    }
#)
#
#gj.add_child(folium.Popup('outline Popup on GeoJSON'))
#gj.add_to(m)


m.add_child(feature_group)
m.add_child(feature_group2)
m.add_child(feature_group3)
m.add_child(feature_group4)
m.add_child(feature_group5)




legend_html = '''
     <div style="position: fixed; 
     bottom: 50px; left: 50px; width: 100px; height: 90px; 
     border:2px solid grey; z-index:9999; font-size:14px;
     ">
     
         &nbsp; Legend
             <br>
                 &nbsp; Home &nbsp; 
                 
                 <i class="fa fa-home fa-2x"
                              style="color:green"></i>
             <br>
        
         &nbsp; Office &nbsp; 
         
         <i class="fa fa-industry fa-2x"
                      style="color:red">
                    
        </i>
                  
                  
      </div>
     '''

In [30]:
m.get_root().html.add_child(folium.Element(legend_html))
m.add_child(folium.map.LayerControl())



In [39]:
m

In [42]:
df_show.head()

created_at                                               text  \
1 2017-09-03 00:25:13  b'Girl \xf0\x9f\x98\x82\xf0\x9f\x98\x82\xf0\x9...   
2 2017-09-03 00:40:04  b"Sorta Kinda but it's considered Fort Lauderd...   
3 2017-09-03 00:41:02  b"Hell yea \xf0\x9f\x98\x85 It's in the plaza ...   
4 2017-09-03 00:42:24  b'Just got yelled at through my messages cause...   
5 2017-09-03 00:46:08   b'Franzy Haitian so idk of Ima get my money fr.'   

       lat      lon  
1  26.2519 -80.1386  
2  26.2519 -80.1386  
3  26.2519 -80.1386  
4  26.2519 -80.1386  
5  26.2519 -80.1386

In [49]:
from folium import plugins

data=[[row['lat'],row['lon']] for index, row in df_show.iterrows()]



hm = plugins.HeatMap(data)
mapa.add_children(hm)

C:\Users\Kamol\Anaconda3\lib\site-packages\ipykernel\__main__.py:8: FutureWarning: Method `add_children` is deprecated. Please use `add_child` instead.


In [45]:
data

[[26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.25189495, -80.1386454],
 [26.1683826, -80.20153450000001],
 [26.1683826, -80.20153450000001],
 [

In [44]:
m

In [51]:
import numpy as np
import pandas as pd
import numpy.ma as ma


def make_data():
    x = np.linspace(-np.pi, np.pi, 101)
    sin = np.sin(x)
    cos = np.cos(x)
    cos[20:50] = np.NaN
    return pd.DataFrame(np.asanyarray([sin, cos]).T, columns=['sin', 'cos'], index=x)

df = make_data()
resolution, width, height = 75, 7, 3

In [57]:
station = '42'
lon, lat = -70, -28
mapa = folium.Map(location=[lat, lon], zoom_start=5)

In [58]:
import base64
import matplotlib.pyplot as plt

fig, ax = plt.subplots(figsize=(width, height))
ax = df.plot(ax=ax, legend=False)
ax.set_ylabel('Sea surface height (m)')
png = 'mpld3_{}.png'.format(station)
fig.savefig(png, dpi=resolution)

encoded = base64.b64encode(open(png, 'rb').read()).decode()

In [59]:
from folium import IFrame

html = '<img src="data:image/png;base64,{}">'.format
iframe = IFrame(html(encoded), width=(width*resolution)+20, height=(height*resolution)+20)
popup = folium.Popup(iframe, max_width=2650)

icon = folium.Icon(color="red", icon="ok")
marker = folium.Marker(location=[lat-2, lon-1], popup=popup, icon=icon)
mapa.add_child(marker);
m.add_child(marker);

In [60]:
from folium import plugins

data=[[row['lat'],row['lon']] for index, row in df_show.iterrows()]



hm = plugins.HeatMap(data)
mapa.add_children(hm)

C:\Users\Kamol\Anaconda3\lib\site-packages\ipykernel\__main__.py:8: FutureWarning: Method `add_children` is deprecated. Please use `add_child` instead.


In [56]:
mapa

In [36]:
mapa

In [46]:
m